In [1]:
%pip install git+https://github.com/huggingface/huggingface_hub

  Cloning https://github.com/huggingface/huggingface_hub to /tmp/pip-req-build-epzdr933
  Running command git clone --filter=blob:none --quiet https://github.com/huggingface/huggingface_hub /tmp/pip-req-build-epzdr933
  Resolved https://github.com/huggingface/huggingface_hub to commit f7529325e0739a0c818f84d50b9642b30918407f
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Created wheel for huggingface-hub: filename=huggingface_hub-0.18.0.dev0-py3-none-any.whl size=300994 sha256=a318ecf0e26f2cb86afe747d4918d8028e1958d535d2ee34a92a1dd8b67016bb
  Stored in directory: /tmp/pip-ephem-wheel-cache-zzrfj0sm/wheels/81/77/10/4ea0848421de7e11b030d8127ca1139b1e0e254f714938175f
Successfully built huggingface-hub


In [2]:
from huggingface_hub import list_models, model_info
from tqdm.contrib.concurrent import thread_map
from huggingface_hub.utils import GatedRepoError, RepositoryNotFoundError
from huggingface_hub import login
from huggingface_hub import HfApi

In [3]:
login()

In [4]:
api = HfApi()

In [5]:
def check_has_readme(model):
    if any([file.rfilename for file in model.siblings if file.rfilename == "README.md"]):
        return True
    return False

In [6]:
models = api.list_models(limit=None,full=True, cardData=True)
models = (model for model in models if model.downloads >20) # must have some downloads
models = (model for model in models if model.likes >3) # must have at least 1 like
models = (model for model in models if model.likes >= 5 or model.downloads >= 200) # must have either many downloads or many likes
models = (model for model in models if check_has_readme(model))

In [7]:
def yield_models_with_files(models):
    for model in models:
        if any([file.rfilename for file in model.siblings if file.rfilename in {"model.safetensors", "pytorch_model.bin"}]):
            yield model
        # if any([file.rfilename for file in model.siblings if file.rfilename.split(".")[-1] in {"onnx"}]):
        #     yield model

In [8]:
models_with_files = list(yield_models_with_files(models))

In [9]:
def bytes_to_mb(bytes_value):
    return bytes_value / (2**20)

In [10]:
def yield_candidate_files(files):
    for file in files:
        if file.rfilename in {"model.safetensors", "pytorch_model.bin"}:
            yield file
        # if file.rfilename.split(".")[-1] in {"onnx"}:
        #     yield file

In [11]:
list(yield_candidate_files(model_info('TaylorAI/gte-tiny').siblings))

[RepoFile: {'blob_id': None, 'lfs': None, 'rfilename': 'model.safetensors', 'size': None},
 RepoFile: {'blob_id': None, 'lfs': None, 'rfilename': 'pytorch_model.bin', 'size': None}]

In [12]:
model_info('TaylorAI/gte-tiny').downloads

32

In [13]:
def check_model_file_below_threshold(model, threshold=50.0):
    try:
        model_id = model.id
        files = api.model_info(model_id, files_metadata=True).siblings
        files = yield_candidate_files(files)
        sizes = (file.size for file in files)
        for size in sizes:
            mb = bytes_to_mb(size)
            if round(mb)< threshold:
                return model_id, mb, model.likes, model.downloads
        return False
    except GatedRepoError:
        return False
    except RepositoryNotFoundError:
        return False

In [14]:
check_model_file_below_threshold(model_info('TaylorAI/gte-tiny'))

('TaylorAI/gte-tiny', 43.351722717285156, 10, 32)

In [15]:
results = thread_map(check_model_file_below_threshold, models_with_files)

  0%|          | 0/3126 [00:00<?, ?it/s]

In [16]:
results = [r for r in results if r]

In [17]:
len(results)

58

In [18]:
results[:10]

[('albert-base-v2', 45.17831230163574, 63, 6608487),
 ('JorisCos/DCCRNet_Libri1Mix_enhsingle_16k', 15.648945808410645, 13, 1214),
 ('JorisCos/DCUNet_Libri1Mix_enhsingle_16k', 37.35937023162842, 4, 594),
 ('WinKawaks/vit-tiny-patch16-224', 21.8319149017334, 5, 4619),
 ('ckiplab/albert-base-chinese-ner', 38.21315860748291, 7, 1825),
 ('ckiplab/albert-base-chinese', 38.4575080871582, 6, 433),
 ('ckiplab/albert-tiny-chinese', 15.443592071533203, 6, 713),
 ('clue/albert_chinese_tiny', 15.807161331176758, 15, 190),
 ('cointegrated/rubert-tiny-sentiment-balanced', 44.96676063537598, 7, 1408),
 ('cointegrated/rubert-tiny-toxicity', 44.96914863586426, 21, 135108)]

In [20]:
from huggingface_hub import create_collection, add_collection_item

In [28]:
description = """Models where the size of the model file (model.safetensors or pytorch_model.bin) < 50mb"""

In [29]:
collection = create_collection("smol models",namespace='librarian-bots',description=description)

In [32]:
for row in sorted(results, key=lambda x: x[-2], reverse=True):
    add_collection_item(collection.slug, row[0],item_type='model', note=f"Model file is {round(row[1])}mb")
